In [149]:
import pickle
import pandas as pd
import os
import time
import lyricsgenius
import json
import azapi
import time
import random
import re

In [156]:
path_to_data = '../SoundOfDownloader/'

In [157]:
tracks_df = pd.read_pickle(f'{path_to_data}tracks_df.pickle')
tracks_df.head()

album_type                album_id                 album_name  \
0      album  6Kssm2LosQ0WyLukFZkEG5                       Demi   
1     single  65L5VcKGKe6sOJIPNFc0Q1           One in a Million   
2     single  5Q5PomrTdI13qpmEeM393B       On My Love (Sped Up)   
3      album  6fpLLJsDSSAlToEDW2jv4F  Animal (Expanded Edition)   
4      album  20Ol6zZ0nLlc5EGTH1zA0j          Delirium (Deluxe)   

  album_release_data                                album_artists_names  \
0         2013-01-01                                        Demi Lovato   
1         2023-08-04    Bebe Rexha:artist_custom_separator:David Guetta   
2         2023-09-12  Zara Larsson:artist_custom_separator:David Guetta   
3         2010-01-01                                              Kesha   
4         2015-11-06                                     Ellie Goulding   

                                   album_artists_ids  album_total_tracks  \
0                             6S2OmqARrzebs0tKUEyXyp                  13   
1  64M6ah0SkkRsnPGtGiRAbb:artist_custom_separator...                   1   
2  1Xylc3o4UrD53lo9CvFvVg:artist_custom_separator...                   4   
3                             6LqNN22kT3074XbTVUrhzX                  18   
4                             0X2BH1fck6amBIoJhDVmmJ                  22   

                                 track_artists_names  \
0                                        Demi Lovato   
1    Bebe Rexha:artist_custom_separator:David Guetta   
2  Zara Larsson:artist_custom_separator:David Guetta   
3                                              Kesha   
4                                     Ellie Goulding   

                                   track_artists_ids  \
0                             6S2OmqARrzebs0tKUEyXyp   
1  64M6ah0SkkRsnPGtGiRAbb:artist_custom_separator...   
2  1Xylc3o4UrD53lo9CvFvVg:artist_custom_separator...   
3                             6LqNN22kT3074XbTVUrhzX   
4                             0X2BH1fck6amBIoJhDVmmJ   

                                          track_name  ...  \
0                                       Heart Attack  ...   
1                                   One in a Million  ...   
2                                         On My Love  ...   
3                                            TiK ToK  ...   
4  Love Me Like You Do - From "Fifty Shades Of Grey"  ...   

                       id                                   uri  \
0  1V6gIisPpYqgFeWbMLI0bA  spotify:track:1V6gIisPpYqgFeWbMLI0bA   
1  3YfGTvsTAWGC2lgoDOikUz  spotify:track:3YfGTvsTAWGC2lgoDOikUz   
2  0K6iKgHPPhAb4Acmg9aD77  spotify:track:0K6iKgHPPhAb4Acmg9aD77   
3  0HPD5WQqrq7wPWR7P7Dw1i  spotify:track:0HPD5WQqrq7wPWR7P7Dw1i   
4  3zHq9ouUJQFQRf3cm1rRLu  spotify:track:3zHq9ouUJQFQRf3cm1rRLu   

                                          track_href  \
0  https://api.spotify.com/v1/tracks/1V6gIisPpYqg...   
1  https://api.spotify.com/v1/tracks/3YfGTvsTAWGC...   
2  https://api.spotify.com/v1/tracks/0K6iKgHPPhAb...   
3  https://api.spotify.com/v1/tracks/0HPD5WQqrq7w...   
4  https://api.spotify.com/v1/tracks/3zHq9ouUJQFQ...   

                                        analysis_url  duration_ms  \
0  https://api.spotify.com/v1/audio-analysis/1V6g...       210840   
1  https://api.spotify.com/v1/audio-analysis/3YfG...       160530   
2  https://api.spotify.com/v1/audio-analysis/0K6i...       222912   
3  https://api.spotify.com/v1/audio-analysis/0HPD...       199693   
4  https://api.spotify.com/v1/audio-analysis/3zHq...       252534   

   time_signature             playlist_id  genre  total_followers  \
0               4  6gS3HhOiI17QNojjPuPzqc    pop          22857.0   
1               4  6gS3HhOiI17QNojjPuPzqc    pop          22857.0   
2               4  6gS3HhOiI17QNojjPuPzqc    pop          22857.0   
3               4  6gS3HhOiI17QNojjPuPzqc    pop          22857.0   
4               4  6gS3HhOiI17QNojjPuPzqc    pop          22857.0   

   total_tracks  
0           428  
1           428  
2           428  
3       

In [158]:
tracks_df.shape

(145732, 37)

In [159]:
def load_from_json(filename):
    """Load data from a JSON file."""
    if os.path.exists(filename):
        with open(filename, 'r') as json_file:
            return json.load(json_file)
    else:
        return {}

In [10]:
def save_to_json(filename, data):
    """Save data to a JSON file."""
    with open(filename, 'w') as json_file:
        json.dump(data, json_file)

In [160]:
# found_tracks = {**found_lyrics, **found_lyrics_2, **found_lyrics_3}
found_tracks = load_from_json('raw_lyrics.json')
len(found_tracks)

38793

In [143]:
# with open('raw_lyrics.json', 'w') as output:
#         json.dump(found_tracks, output, indent=2)

In [161]:
not_found_tracks = tracks_df[~tracks_df['id'].isin(found_tracks)]
not_found_tracks.shape

(94433, 37)

In [162]:
not_found_tracks.drop_duplicates(['id'], inplace=True)

/var/folders/n0/3nrmklqn7ggc7d77_rjbg2k40000gn/T/ipykernel_15992/1089900416.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  not_found_tracks.drop_duplicates(['id'], inplace=True)


In [165]:
not_found_tracks.shape

(88204, 37)

In [167]:
not_found_tracks.to_csv('not_found_tracks.csv', index=False)

In [9]:
def save_to_pickle(filename, data):
    """Append data to a pickle file."""
    existing_data = load_from_pickle(filename)
    existing_data.update(data)
    
    with open(filename, 'wb') as file:
        pickle.dump(existing_data, file)

def load_from_pickle(filename):
    """Load data from a pickle file."""
    if os.path.exists(filename):
        with open(filename, 'rb') as file:
            return pickle.load(file)
    else:
        return {}

In [164]:
import re

def remove_patterns(song_name):
    patterns_to_remove = [
        r'\s*-\s*[\w\'\(\)\[\]]*\s*(?:[vV]ersion|[rR]emix|[rR]emaster|[aA]coustic|[sS]ingle|RMX|[rR]emastered|B-side|[rR]adio|[eE]dit|Live|[uU]nplugged|[dD]emo|Bonus|Idol|Season|Session|[sS]tripped|[mM]ix|[sS]tudio)\s*\w*',
        r'\s*\[[^\]]*(?:[Ff]eat\.|ft\.)[^\]]*\]\s*',
        r'\s*-\s*Remix\s*.*',
        r'\s*-\s*\d{4}\s*',
        r'\s*From\s*".*?"\s*[sS}oundtrack|[mM]otion [Pp]icture|[sS]eries\s*',
        'Spider-Man: Into the Spider-Verse',
        r'/\s*\w*\s*Version',
        r'\s*Theme from\s*".*?"\s*',
        r'\s*\[[^\]]*(?:[Ff]eat\.|[Ff]t\.)[^\]]*\]\s*',
        r'\(feat\.[^\)]*\)',
        r'\(from\s*".*?"\)', 
        r'\(Live|Acoustic|Remix\)',
        r'\(\*\w+\s*Remaster\)',

    ]

    for pattern in patterns_to_remove:
        song_name = re.sub(pattern, '', song_name)

    # Remove extra whitespaces
    song_name = re.sub(r'\s+', ' ', song_name).strip()

    return song_name

In [99]:
def contains_non_latin(text):
    try:
        text.encode('ascii')
        return False
    except UnicodeEncodeError:
        return True

In [101]:
not_found_tracks = not_found_tracks[~not_found_tracks['track_name'].apply(contains_non_latin)]

In [114]:
not_found_tracks['track_name'] = not_found_tracks['track_name'].apply(remove_patterns)
not_found_tracks.head()

album_type                album_id           album_name  \
200      album  6r7LZXAVueS5DqdrvXJJK7  Paranoid (Remaster)   
250      album  4FA68GsblSfvKZZRfM1tI1              Dynasty   
371      album  4MtX90BJLKOVHG36jV9oaR          Grand Champ   
490      album  10ZcEPnqq7VPUfGytiVTuw        Feels So Good   
777      album  7rbdgYKz1DI4gXMWveqS5T         OK ORCHESTRA   

    album_release_data album_artists_names       album_artists_ids  \
200         1970-09-18       Black Sabbath  5M52tdBnJaKSvOpJGz8mfZ   
250         1979-03-23                KISS  07XSN3sPlIlB2L2XNcTwJw   
371         2003-01-01                 DMX  1HwM5zlC5qNWhJtM00yXzG   
490         2002-09-09       Atomic Kitten  6JMHws5haIO6V35YNYDnDw   
777         2021-03-26                 AJR  6s22t5Y3prQHyaHWUN1R1C   

     album_total_tracks track_artists_names       track_artists_ids  \
200                   8       Black Sabbath  5M52tdBnJaKSvOpJGz8mfZ   
250                   9                KISS  07XSN3sPlIlB2L2XNcTwJw   
371                  24                 DMX  1HwM5zlC5qNWhJtM00yXzG   
490                  15       Atomic Kitten  6JMHws5haIO6V35YNYDnDw   
777                  13                 AJR  6s22t5Y3prQHyaHWUN1R1C   

                    track_name  ...                      id  \
200                   Paranoid  ...  1Y373MqadDRtclJNdnUXVc   
250  I Was Made For Lovin' You  ...  07q0QVgO56EorrSGHC48y3   
371       X Gon' Give It To Ya  ...  66orjI5vOkyxOZLHWrPklh   
490           The Tide Is High  ...  1QhSB9L9M5eZQhW4RNOhXK   
777    World's Smallest Violin  ...  68EkhVWIeULhHxcbi1QhzK   

                                      uri  \
200  spotify:track:1Y373MqadDRtclJNdnUXVc   
250  spotify:track:07q0QVgO56EorrSGHC48y3   
371  spotify:track:66orjI5vOkyxOZLHWrPklh   
490  spotify:track:1QhSB9L9M5eZQhW4RNOhXK   
777  spotify:track:68EkhVWIeULhHxcbi1QhzK   

                                            track_href  \
200  https://api.spotify.com/v1/tracks/1Y373MqadDRt...   
250  https://api.spotify.com/v1/tracks/07q0QVgO56Eo...   
371  https://api.spotify.com/v1/tracks/66orjI5vOkyx...   
490  https://api.spotify.com/v1/tracks/1QhSB9L9M5eZ...   
777  https://api.spotify.com/v1/tracks/68EkhVWIeULh...   

                                          analysis_url  duration_ms  \
200  https://api.spotify.com/v1/audio-analysis/1Y37...       168406   
250  https://api.spotify.com/v1/audio-analysis/07q0...       271240   
371  https://api.spotify.com/v1/audio-analysis/66or...       219733   
490  https://api.spotify.com/v1/audio-analysis/1QhS...       206093   
777  https://api.spotify.com/v1/audio-analysis/68Ek...       180747   

     time_signature             playlist_id       genre  total_followers  \
200               4  7dowgSWOmvdpwNkGFMUs6e        rock          11100.0   
250               4  7dowgSWOmvdpwNkGFMUs6e        rock          11100.0   
371               4  6MXkE0uYF4XwU4VTtyrpfP     hip hop          11419.0   
490               4  2ZIRxkFuqNPMnlY7vL54uK   dance pop          14584.0   
777               4  3ByKGRaNhQrtrvuGdjQ2Vf  pov: indie           1281.0   

     total_tracks  
200           513  
250           513  
371           350  
490           340  
777           396  

[5 rows x 37 columns]

In [109]:
total_rows = len(not_found_tracks)
batch_size = 50

for start in range(0, total_rows, batch_size):
    end = min(start + batch_size, total_rows)
    batch = not_found_tracks['track_name'].apply(remove_patterns).iloc[start:end]
    print(batch)

200                                              Paranoid
250                             I Was Made For Lovin' You
371                                  X Gon' Give It To Ya
490                                      The Tide Is High
777                               World's Smallest Violin
798                                          LIFE'S A BIT
961                                             Glycerine
1056                                      Bout Dat Action
1082    Ain't No Way Around It Remix feat. Future, Big...
1130                                       The Radio Edit
1146                            Awake In A Dream 2 winner
1151                                      Something More)
1154                                         Whatta Night
1156                                          Give It Up)
1167                                                Sugar
1168                                         Shake It Off
1173                                         Mr. Immature
1176          

KeyboardInterrupt: 

In [116]:
class LyricsScraper:
    def __init__(self, access_token):
        self.genius = lyricsgenius.Genius(access_token)
        self.found_lyrics_dict = {}
        self.not_found_tracks = set()
        self.counter = 0
        self.save_interval = 3

    def get_lyrics_and_save(self, row, found_lyrics_json='found_lyrics_2.json', not_found_tracks_json='not_found_tracks_2.json'):
        song_title = row['track_name']
        artist_name = row['track_artists_names']
        track_id = row['track_id']

        result = {'track_id': track_id, 'found_lyrics': None, 'not_found_lyrics': None}

        try:
            artists = artist_name.split(':artist_custom_separator:')            
            # Check if lyrics are already found for this track_id
            if track_id in self.found_lyrics_dict:
                print(f"Skipping {song_title} by {artist_name} as lyrics are already found.")
                result['found_lyrics'] = self.found_lyrics_dict[track_id]['lyrics']
            else:
                for artist in artists:
                    artist = artist.strip()
                    print(artist)
                    found_song = self._fetch_song_object(song_title, artist)
                    if found_song and self._is_valid_match(found_song, song_title, artist):
                        # Store additional information in the dictionary
                        self.found_lyrics_dict[track_id] = {
                            'lyrics': found_song.lyrics,
                            'path': found_song.path,
                            'artist': found_song.artist,
                            'title': found_song.title
                        }
                        result['found_lyrics'] = found_song.lyrics
                        self.counter += 1
                        if self.counter % self.save_interval == 0:
                            print(f"Processed {self.counter} songs. Saving to JSONs...")
                            self.save_to_json(found_lyrics_json, self.found_lyrics_dict)
                            self.save_to_json(not_found_tracks_json, list(self.not_found_tracks))
                    else:
                        if artist == artists[-1]:
                            print('Fail')
                            self.not_found_tracks.add(track_id)
                            result['not_found_lyrics'] = f'Lyrics for {song_title} by {artist_name} not found or not a valid match.'
                        else:
                            print('ok, try one more time')

        except Exception as e:
            print(f"An error occurred while processing {song_title} by {artist_name}: {e}")

        return result

    def _fetch_song_object(self, song_title, artist_name, max_retries=3):
        """
        Fetch lyrics based on the specified search option.

        Parameters:
        - song_title: Title of the song
        - artist_name: Name of the artist
        """
        for _ in range(max_retries):
            try:
                # Split the artists in case there are multiple
                    song = self.genius.search_song(song_title, artist_name, get_full_info=False)
                    if song: # and self._is_valid_match(song, song_title, artist_name)
                        return song
            except Exception as e:
                print(f"An error occurred: {e}")
                time.sleep(3)

        return None

    def _is_valid_match(self, song, target_title, target_artist):
        return (
            song.title.lower() in target_title.lower()
        )

    def save_to_json(self, filename, data):
        """Save data to a JSON file."""
        with open(filename, 'w') as json_file:
            json.dump(data, json_file)

    def load_from_json(self, filename):
        """Load data from a JSON file."""
        if os.path.exists(filename):
            with open(filename, 'r') as json_file:
                return json.load(json_file)
        else:
            return {}

In [118]:
genius_access_token = 'Z84JqtWpVJYD9enF2sshfrJtNw1c7MiO25ehQV1DIZ_6DHsQiZtEfiA1xuwyDjNbyX-1xGszX_sIPlJp6X0weA'
lyrics_scraper = LyricsScraper(genius_access_token)

In [117]:
not_found_tracks.shape


(77870, 37)

In [119]:
# Iterate over DataFrame rows and fetch lyrics
for index, row in not_found_tracks.iterrows():
    try:
        lyrics = lyrics_scraper.get_lyrics_and_save(row)
        print(index, lyrics)
    except Exception as e:
        print(f"An error occurred: {e}")

Black Sabbath
Searching for "Paranoid" by Black Sabbath...
An error occurred: Request timed out:
HTTPSConnectionPool(host='genius.com', port=443): Read timed out. (read timeout=5)
Searching for "Paranoid" by Black Sabbath...
Done.
200 {'track_id': '1Y373MqadDRtclJNdnUXVc', 'found_lyrics': "99 ContributorsTranslationsFrançaisParanoid Lyrics[Intro]\n\n[Verse 1]\nFinished with my woman\n'Cause she couldn't help me with my mind\nPeople think I'm insane\nBecause I am frowning all the time\n\n[Verse 2]\nAll day long I think of things\nBut nothing seems to satisfy\nThink I'll lose my mind\nIf I don't find something to pacify\n\n[Bridge]\nCan you help me\nOccupy my brain?\nOh yeah\n\n[Verse 3]\nI need someone to show me\nThe things in life that I can't find\nI can't see the things that make true happiness\nI must be blind\n\n[Guitar Solo]\nYou might also like[Verse 4]\nMake a joke and I will sigh\nAnd you will laugh and I will cry\nHappiness I cannot feel\nAnd love to me is so unreal\n\n[Verse

KeyboardInterrupt: 

In [136]:
class AZLyricsScraper:
    def __init__(self):
        self.api = azapi.AZlyrics('google', 0.4)
        self.found_lyrics_dict = {}
        self.counter = 0
        self.not_found_tracks = []
        self.save_interval = 2 
        self.request_interval = 5
        # self.user_agent = UserAgent().random
        # self.proxies = self.load_proxies()

    def load_proxies(self):
        """Load proxies from a text file."""
        try:
            with open('http_proxies_elite.txt', 'r') as file:
                proxies = file.read().splitlines()
                return [{'http': f'http://{proxy}'} for proxy in proxies]
        except FileNotFoundError:
            print("Proxy file not found.")
            return []

    def get_random_proxy(self):
        """Select a random proxy from the list."""
        return random.choice(self.proxies)

    def get_lyrics_and_save(self, row, found_lyrics_json='found_lyrics_azlyrics.json', not_found_lyrics_json='not_found_tracks_azlyrics.json'):
        # перезаписвает json'ы, лучше переделать, чтобы добавлял к существующему
        result = {'found_lyrics': None, 'not_found_lyrics': None}

        try:
            artist_name = ' '.join(row['track_artists_names'].split(':artist_custom_separator:'))
            title_name = row['track_name']
            track_id = row['track_id']

            # Check if lyrics are already found for this track_id
            if track_id in self.found_lyrics_dict:
                print(f"Skipping {title_name} by {artist_name} as lyrics are already found.")
                result['found_lyrics'] = self.found_lyrics_dict[track_id]['lyrics']
            else:
                self.api.artist = artist_name
                self.api.title = title_name

                # Switch user agent and proxy for each request
                # self.api.proxies = self.get_random_proxy()
                # self.api.headers = {'User-Agent': self.user_agent}

                # Get lyrics using AZLyrics API
                lyrics = self.api.getLyrics(save=False)
                # print(f'Lyrics are {lyrics}')
                self.counter += 1

                if lyrics:
                    # Store additional information in the dictionary
                    self.found_lyrics_dict[track_id] = {
                        'lyrics': lyrics,
                        'artist': self.api.artist,
                        'title': self.api.title
                    }
                    result['found_lyrics'] = lyrics

                    if self.counter % self.save_interval == 0:
                        print(f"Processed {self.counter} songs. Saving to JSONs...")
                        self.save_to_json(found_lyrics_json, self.found_lyrics_dict)
                        self.save_to_json(not_found_lyrics_json, self.not_found_tracks)
                else:
                    result['not_found_lyrics'] = f'Lyrics not found for {title_name} by {artist_name}.'
                    self.not_found_tracks.append(track_id)
                    if self.counter % self.save_interval == 0:
                        self.save_to_json(not_found_lyrics_json, self.not_found_tracks)
                    print(result['not_found_lyrics'])

                print('sleeping...')
                time.sleep(self.request_interval)
        except Exception as e:
            print(f"An error occurred: {e}")

        return result

    def save_to_json(self, filename, data):
        """Save data to a JSON file."""
        with open(filename, 'w') as file:
            json.dump(data, file)

    def load_from_json(self, filename):
        """Load data from a JSON file."""
        if os.path.exists(filename):
            with open(filename, 'r') as json_file:
                return json.load(json_file)
        else:
            return []


In [137]:
scraper = AZLyricsScraper()

In [138]:
for index, row in not_found_tracks.iterrows():
    try:
        print(f'try row {index}')
        result = scraper.get_lyrics_and_save(row)
    except Exception as e:
        print(f"An error occurred for row {index}: {e}")

try row 0
sleeping...
try row 1
Similarity < 0.4
Lyrics not found for Ever Fallen in Love (With Someone You Shouldn't've?) Version by Buzzcocks.
sleeping...
try row 2
sleeping...
try row 3
Processed 4 songs. Saving to JSONs...
sleeping...
try row 4
sleeping...
try row 5
An error occurred: list index out of range
try row 6
Google found nothing!
Lyrics not found for Are You Drinkin' With Me Jesus by Jello Biafra Mojo Nixon.
sleeping...
try row 7
sleeping...
try row 8
Similarity < 0.4
Lyrics not found for That's Progress by D.O.A..
sleeping...
try row 9
Google found nothing!
Lyrics not found for Millwall Boys by Sham 69.
sleeping...
try row 10
Processed 10 songs. Saving to JSONs...
sleeping...
try row 11
An error occurred: list index out of range
try row 12
sleeping...
try row 13
Similarity < 0.4
Lyrics not found for What's Next? by OFF!.
sleeping...
try row 14
Google found nothing!
Lyrics not found for Rise - Bob Clearmountain Remix by Public Image Ltd. Bob Clearmountain.
sleeping...
try

KeyboardInterrupt: 